In [1]:
import madrigalWeb.madrigalWeb as mw
from io import StringIO
import numpy as np
import matplotlib.pyplot as plt

In [2]:
# Path to Madrigal server
madURL = "https://madrigal.eiscat.se/madrigal"

# Madrigal logs user details
UserName = "Insert your name"
UserEmail = "Insert your email address"
UserAffiliation = "Insert your affiliation"

In [3]:
# Create data object
madData = mw.MadrigalData(madURL)

In [4]:
# Instrument codes:
# 70: EISCAT multistatic vector data
# 71: EISCAT Kiruna UHF receiver
# 72: EISCAT UHF radar
# 73: EISCAT Sodankylä UHF receiver
# 74: EISCAT VHF radar
# 75: EISCAT Kiruna VHF receiver
# 76: EISCAT Sodankylä VHF receiver
# 95: EISCAT Svalbard radar
# 2950: EISCAT Tromsø Dynasonde
# 2951: EISCAT Svalbard dynasonde
madInstruments = [72]

In [5]:
# List UHF experiments during April 2, 2019
madExps = madData.getExperiments(madInstruments, 2019, 4, 2, 0, 0, 0, 2019, 4, 2, 23, 59, 59, 1)

In [6]:
for madExp in madExps:
    print(madExp.name)

2019-04-02_beata@uhfa


In [7]:
# There is only one UHF experiment for this day. Find its ID and URL
expID = madExp.id
expURL = madExp.url
print(expID)
print(expURL)

20010215
https://madrigal.eiscat.se/madrigal/madtoc/experiments/2019/tro/02apr19


In [8]:
# List the files from this experiment and their kind of data (kindat)
expFiles = madData.getExperimentFiles(expID)
for expFile in expFiles:
    print(expFile.name)
    print(expFile.kindat)

/opt/madrigal/experiments/2019/tro/02apr19/MAD6400_2019-04-02_beata_60@uhfa.hdf5
6400
/opt/madrigal/experiments/2019/tro/02apr19/MAD6301_2019-04-02_beata_60@uhfa.hdf5
6301
/opt/madrigal/experiments/2019/tro/02apr19/MAD6300_2019-04-02_beata_60@uhfa.hdf5
6300


In [9]:
# Kindat 6400 is standard GUISDAP analysis, 63nn are raw power profiles from different decodings. Select the analysis.
expFile = expFiles[0]
print(expFile.name)

/opt/madrigal/experiments/2019/tro/02apr19/MAD6400_2019-04-02_beata_60@uhfa.hdf5


In [11]:
# The isprint method of MadrigalData can be used to extract and filter the results
# We extract these analysed or derived parameters:
# ut1_unix: start time
# gdalt: altitude over geodetic sea level
# ne: electron density
# te: electron temperature
# ti: ion temperature
# We apply the following restrictions:
# 100 km < gdalt < 400 km
expTxt = madData.isprint(expFile.name, 'ut1_unix,gdalt,ne,ti,te', 'filter=gdalt,100,400', UserName, UserEmail, UserAffiliation)
# isprint returns ASCII string, convert it to numpy array
expData = np.loadtxt(StringIO(expTxt))

ValueError: unable to open url https://madrigal.eiscat.se/madrigal/isprintService.py?file=%2Fopt%2Fmadrigal%2Fexperiments%2F2019%2Ftro%2F02apr19%2FMAD6400_2019-04-02_beata_60@uhfa.hdf5&parms=ut1_unix+gdalt+ne+ti+te&filters=filter%3Dgdalt%2C100%2C400&user_fullname=Insert+your+name&user_email=Insert your email address&user_affiliation=Insert+your+affiliation

In [ ]:
# Plot the profiles from the first timestep
hh = expData[0:24,1]
Ne = expData[0:24,2]
Ti = expData[0:24,3]
Te = expData[0:24,4]
fig, (ax1, ax2) = plt.subplots(1, 2)
ax1.plot(Ne, hh)
ax1.semilogx()
ax1.set_title('Electron density')
ax1.set_xlabel('m-3')
ax1.set_ylabel('km')
ax2.plot(Ti, hh, label=("Ion temperature"))
ax2.plot(Te, hh, label=("Electron temperature"))
ax2.set_xlabel('K')
ax2.legend()
plt.show()